# Métodos de orden superior

## Método de Taylor

1. Crear una función que reciba una función f y un valor k y devuelva la derivada total k-ésima de f.
2. Programar el método de Taylor.
3. Aplicar el método de Taylor de orden 3 al problema de valor inicial $$x' = t(1-x^2),\quad x(0)=0.$$ Aproximar la solución en $t=2$ con 20 pasos y comparar los resultados obtenidos con el método de Euler.
4. Comparar el error cometido al estimar $x(2)$ para la solución del PVI $$x' = x,\quad x(0)=1$$ con los métodos de Taylor de orden $1,2,3,4,5$ y  número de pasos entre 10 y 100.
5. Aproximar $x(2)$ para la solución del PVI $$x' = x,\quad x(0)=1$$ con el método de Taylor de orden $3$. Aproximar el error con usando el método de Taylor de orden $4$. Comparar la estimación del error con el valor exacto.

In [1]:
f(t,x) = t*(1-x^2)

In [3]:
@cached_function
def derivada_total(f,k):
    # Sólo funciona si f depende de t y de otras variables
    if k == 0:
        return f
    dta = derivada_total(f,k-1)
    return (dta.diff()*vector([1,f])).expand()

In [4]:
@cached_function
def derivada_total_autonomo_escalar(f,k):
    if k == 0:
        return f
    dta = derivada_total(f,k-1)
    return (dta.diff(x)*f).expand()

In [23]:
derivada_total(f,0)

(t, x) |--> -(x^2 - 1)*t

In [24]:
derivada_total(f,1)

(t, x) |--> 2*t^2*x^3 - 2*t^2*x - x^2 + 1

In [25]:
derivada_total(f,2)

(t, x) |--> -6*t^3*x^4 + 8*t^3*x^2 + 6*t*x^3 - 2*t^3 - 6*t*x

In [28]:
factorial(5)

120

In [40]:
def T(f,h,k):
    return sum([ derivada_total(f,i)*h^i/factorial(i+1) 
                                      for i in [0 .. k-1]])

In [41]:
var('t,x,h')
T(f,h,3)

(t, x) |--> -1/3*(3*t^3*x^4 - 4*t^3*x^2 - 3*t*x^3 + t^3 + 3*t*x)*h^2 + 1/2*(2*t^2*x^3 - 2*t^2*x - x^2 + 1)*h - (x^2 - 1)*t

In [44]:
def taylor(f,a,x0,b,n,k):
    ''' 
    Método de Taylor
    Recibe la función f, ....
    Calcula la solución aprox de x'=f(t,x) 
    mediante el método de Taylor de n pasos
    Devuelve una lista con los puntos (tk,xk) obtenidos
    '''
    h = (b-a)/n
    tk = [a.n(), a+h .. b]
    xk = [x0]*(n+1)
    phi(t,x) = T(f,h,k)
    for i in [1 .. n]:
        xk[i] = xk[i-1] + h*phi(tk[i-1],xk[i-1])
    puntos = list(zip(tk,xk))
    return puntos

In [52]:
# Valores iniciales, finales y número de pasos
f(t,x) = t*(1-x^2)
a = 0.
x0 = 0.
b = 2

In [55]:
line(taylor(f,a,x0,b,10,3)) + plot_slope_field(f,(t,0,2),(x,0,1))

## Método de Runge-Kutta

1. Crea una función que reciba la tabla de Butcher de un método de Runge-Kutta, la aproximación $(t_n,x_n)$ y la función que define el campo de la ecuación diferencial y calcule un paso del método de Runge-Kutta.
2. Crea una función que reciba la tabla de Butcher, el PVI, el valor final del tiempo $b$ y el número de pasos $n$ y devuelva la aproximación de la solución del PVI en $t=b$ mediante $n$ pasos del método de Runge-Kutta.
3. Aplicar el método de Runge-Kutta de cuarto orden al PVI $$x'=t(1-x^2),\quad x(0)=0.$$ Aproximar la solución con 20 pasos y comparar los resultados obtenidos con el método de Euler y el anterior de Taylor de orden 4. Además, comparar los resultados con el comando de Sage `desolve_rk4`.
4. Aproximar $x(2)$ para la solución del PVI $$x' = x,\quad x(0)=1$$ con el método de Runge-Kutta-Fehlberg, usando el método de orden $4$ para aproximar la solución y el de orden $5$ para aproximar el error. Comparar la estimación del error con el valor exacto.

In [47]:
RK4 = matrix([[  0,   0,   0,   0,   0],
              [1/2, 1/2,   0,   0,   0],
              [1/2,   0, 1/2,   0,   0],
              [  1,   0,   0,   1,   0],
              [  0, 1/6, 1/3, 1/3, 1/6]])
show(RK4)

[  0   0   0   0   0]
[1/2 1/2   0   0   0]
[1/2   0 1/2   0   0]
[  1   0   0   1   0]
[  0 1/6 1/3 1/3 1/6]

In [48]:
vector(RK4[:-1,0]), vector(RK4[-1,1:]), matrix(RK4[:-1,1:])

(
                                        [  0   0   0   0]
                                        [1/2   0   0   0]
                                        [  0 1/2   0   0]
(0, 1/2, 1/2, 1), (1/6, 1/3, 1/3, 1/6), [  0   0   1   0]
)

In [50]:
def butcher(T):
    theta = vector(T[:-1,0])
    alpha = vector(T[-1,1:])
    Alpha = matrix(T[:-1,1:])
    return theta, alpha, Alpha

In [51]:
theta, alpha, Alpha = butcher(RK4)
theta, alpha, Alpha

(
                                        [  0   0   0   0]
                                        [1/2   0   0   0]
                                        [  0 1/2   0   0]
(0, 1/2, 1/2, 1), (1/6, 1/3, 1/3, 1/6), [  0   0   1   0]
)

In [52]:
f(t,x) = t*(1-x^2)
t0 = 0 
x0 = 0 
h = 1/10

In [53]:
tau = vector(RDF,[t0 + k for k in theta*h])
tau

(0.0, 0.05, 0.05, 0.1)

In [54]:
eta = vector(RDF,[x0 for k in alpha])
eta

(0.0, 0.0, 0.0, 0.0)

In [39]:
m = eta.length() - 1

In [40]:
for mu in [1 .. m]:
    for k in [0 .. mu-1]:
        eta[mu] += h * Alpha[mu,k]*f(tau[k],eta[k])
eta

(0.000000000000000, 0.000000000000000, 0.00250000000000000, 0.00499996875000000)

In [61]:
def phiRK(theta,alpha,Alpha,t0,x0,h,f):
    tau = vector(RDF,[t0 + k for k in theta*h])
    eta = vector(RDF,[x0 for k in alpha])
    m = eta.length() - 1
    for mu in [1 .. m]:
        for k in [0 .. mu-1]:
            eta[mu] += h * Alpha[mu,k]*f(tau[k],eta[k])
    x1 = x0
    for mu in [0 .. m]:
        x1 += h*alpha[mu]*f(tau[mu],eta[mu])
    return x1

In [62]:
phiRK(theta,alpha,Alpha,t0,x0,h,f)

0.004999947917187499

In [63]:
def RK(f,a,x0,b,n,T):
    ''' 
    Método de Runge Kutta
    Recibe la función f, ....
    Calcula la solución aprox de x'=f(t,x) 
    mediante el método de Runge-Kutta
    Devuelve una lista con los puntos (tk,xk) obtenidos
    '''
    h = (b-a)/n
    tk = [a.n(), a+h .. b]
    xk = [x0]*(n+1)
    theta, alpha, Alpha = butcher(T)
    for i in [1 .. n]:
        xk[i] = phiRK(theta,alpha,Alpha,tk[i-1],xk[i-1],h,f)
    puntos = list(zip(tk,xk))
    return puntos

In [68]:
RK(f,0.,0.,2.,20,RK4),\
desolve_rk4(f(t,x),x,ics=[0,0],end_points=2,step=0.1)

([(0.000000000000000, 0.000000000000000),
  (0.100000000000000, 0.00499994791718750),
  (0.200000000000000, 0.0199972921054024),
  (0.300000000000000, 0.0449695560459070),
  (0.400000000000000, 0.0798296038747933),
  (0.500000000000000, 0.124352747294756),
  (0.600000000000000, 0.178080511333377),
  (0.700000000000000, 0.240212399094062),
  (0.800000000000000, 0.309506346508372),
  (0.900000000000000, 0.384218323800434),
  (1.00000000000000, 0.462116342858547),
  (1.10000000000000, 0.540596886420834),
  (1.20000000000000, 0.616907944921907),
  (1.30000000000000, 0.688446368410043),
  (1.40000000000000, 0.753063038408892),
  (1.50000000000000, 0.809296965762532),
  (1.60000000000000, 0.856479353464563),
  (1.70000000000000, 0.894692719289639),
  (1.80000000000000, 0.924615901854427),
  (1.90000000000000, 0.947312178945583),
  (2.00000000000000, 0.964018056365601)],
 [[0, 0],
  [0.1, 0.004999947917187499],
  [0.2, 0.01999729210540237],
  [0.3, 0.04496955604590699],
  [0.4, 0.079829603874

## Sistemas de ecuaciones

1. Aplicar  los métodos de Taylor y Runge-Kutta (ambos de cuarto orden) al problema de valor inicial
$$x'=-y+x^2,\quad y'=x,\quad x(0)=0.3,\quad y(0)=0.$$
con tamaño de paso $h=0.1$ y $n=50,100,500,1000$.

In [23]:
def derivada_total(f,k):
    if k == 0:
        return f
    dt = copy(f)
    for _ in range(k):
        dt = dt.diff()*f
    return dt

In [24]:
def T(f,h,k):
    return sum([ derivada_total(f,i)*h^i/factorial(i+1) 
                                      for i in [0 .. k-1]])

In [27]:
def taylor(f,x0,h,n,k):
    ''' 
    Método de Taylor
    Recibe la función f, ....
    Calcula la solución aprox de x'=f(x) 
    mediante el método de Taylor de n pasos
    Devuelve una lista con los puntos (tk,xk) obtenidos
    '''
    xk = [vector(RDF,x0)]*(n+1)
    phi = T(f,h,k)
    for i in [1 .. n]:
        xk[i] = xk[i-1] + h*phi(*xk[i-1])
    return xk

In [14]:
X(x,y) = [-y+x^2,x]

In [34]:
line(taylor(X,[0.3,0],0.1,1000,4)) \
+ plot_vector_field(X(x,y),(x,-0.5,0.5),(y,-0.5,0.5))